In [1]:
import numpy as np # library to handle data in a vectorized manner

import pandas as pd # library for data analsysis
pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)

import json # library to handle JSON files

!conda install -c conda-forge geopy --yes # uncomment this line if you haven't completed the Foursquare API lab
from geopy.geocoders import Nominatim # convert an address into latitude and longitude values

import requests # library to handle requests
from pandas.io.json import json_normalize # tranform JSON file into a pandas dataframe

# Matplotlib and associated plotting modules
import matplotlib.cm as cm
import matplotlib.colors as colors

# import k-means from clustering stage
from sklearn.cluster import KMeans

!conda install -c conda-forge folium=0.5.0 --yes # uncomment this line if you haven't completed the Foursquare API lab
import folium # map rendering library

print('Libraries imported.')

Solving environment: done

## Package Plan ##

  environment location: /home/jupyterlab/conda/envs/python

  added / updated specs:
    - geopy


The following packages will be downloaded:

    package                    |            build
    ---------------------------|-----------------
    ca-certificates-2020.4.5.2 |       hecda079_0         147 KB  conda-forge
    certifi-2020.4.5.2         |   py36h9f0ad1d_0         152 KB  conda-forge
    geographiclib-1.50         |             py_0          34 KB  conda-forge
    geopy-1.22.0               |     pyh9f0ad1d_0          63 KB  conda-forge
    ------------------------------------------------------------
                                           Total:         395 KB

The following NEW packages will be INSTALLED:

  geographiclib      conda-forge/noarch::geographiclib-1.50-py_0
  geopy              conda-forge/noarch::geopy-1.22.0-pyh9f0ad1d_0

The following packages will be UPDATED:

  ca-certificates                     2020.4.5

In [2]:
!pip install lxml

     |████████████████████████████████| 5.5MB 5.0MB/s eta 0:00:01


In [3]:
import lxml

In [4]:
df = pd.read_html('https://en.wikipedia.org/wiki/List_of_postal_codes_of_Canada:_M')[0]

In [5]:
df.head()

Postal Code           Borough               Neighborhood
0         M1A      Not assigned               Not assigned
1         M2A      Not assigned               Not assigned
2         M3A        North York                  Parkwoods
3         M4A        North York           Victoria Village
4         M5A  Downtown Toronto  Regent Park, Harbourfront

In [6]:
df_dropna = df[df.Borough != "Not assigned"].reset_index(drop=True)
df_dropna.head()

Postal Code           Borough                                 Neighborhood
0         M3A        North York                                    Parkwoods
1         M4A        North York                             Victoria Village
2         M5A  Downtown Toronto                    Regent Park, Harbourfront
3         M6A        North York             Lawrence Manor, Lawrence Heights
4         M7A  Downtown Toronto  Queen's Park, Ontario Provincial Government

In [7]:
df_grouped = df_dropna.groupby(["Postal Code", "Borough"], as_index=False).agg(lambda x: ", ".join(x))
df_grouped.head()

Postal Code      Borough                            Neighborhood
0         M1B  Scarborough                          Malvern, Rouge
1         M1C  Scarborough  Rouge Hill, Port Union, Highland Creek
2         M1E  Scarborough       Guildwood, Morningside, West Hill
3         M1G  Scarborough                                  Woburn
4         M1H  Scarborough                               Cedarbrae

In [8]:
for index, row in df_grouped.iterrows():
    if row["Neighborhood"] == "Not assigned":
        row["Neighborhood"] = row["Borough"]
        
df_grouped.head()

Postal Code      Borough                            Neighborhood
0         M1B  Scarborough                          Malvern, Rouge
1         M1C  Scarborough  Rouge Hill, Port Union, Highland Creek
2         M1E  Scarborough       Guildwood, Morningside, West Hill
3         M1G  Scarborough                                  Woburn
4         M1H  Scarborough                               Cedarbrae

In [9]:
column_names = ["Postal Code", "Borough", "Neighborhood"]

In [10]:
test_df = pd.DataFrame(columns=column_names)

In [11]:
test_list = ["M5G", "M2H", "M4B", "M1J", "M4G", "M4M", "M1R", "M9V", "M9L", "M5V", "M1B", "M5A"]

In [12]:
for postcode in test_list:
    test_df = test_df.append(df_grouped[df_grouped["Postal Code"]==postcode], ignore_index=True)
    
test_df.head()

Postal Code           Borough                     Neighborhood
0         M5G  Downtown Toronto               Central Bay Street
1         M2H        North York                Hillcrest Village
2         M4B         East York  Parkview Hill, Woodbine Gardens
3         M1J       Scarborough              Scarborough Village
4         M4G         East York                          Leaside

In [13]:
df2 = pd.read_csv("Geospatial_Coordinates.csv")
df2.head()

Postal Code   Latitude  Longitude
0         M1B  43.806686 -79.194353
1         M1C  43.784535 -79.160497
2         M1E  43.763573 -79.188711
3         M1G  43.770992 -79.216917
4         M1H  43.773136 -79.239476

In [14]:
df2.rename(columns={"Postal Code": "Postal Code"}, inplace=True)
df2.head()

Postal Code   Latitude  Longitude
0         M1B  43.806686 -79.194353
1         M1C  43.784535 -79.160497
2         M1E  43.763573 -79.188711
3         M1G  43.770992 -79.216917
4         M1H  43.773136 -79.239476

In [15]:
df_3 = df_grouped.merge(df2, on='Postal Code', how="left")
df_3.head()

Postal Code      Borough                            Neighborhood   Latitude  \
0         M1B  Scarborough                          Malvern, Rouge  43.806686   
1         M1C  Scarborough  Rouge Hill, Port Union, Highland Creek  43.784535   
2         M1E  Scarborough       Guildwood, Morningside, West Hill  43.763573   
3         M1G  Scarborough                                  Woburn  43.770992   
4         M1H  Scarborough                               Cedarbrae  43.773136   

   Longitude  
0 -79.194353  
1 -79.160497  
2 -79.188711  
3 -79.216917  
4 -79.239476

In [16]:
column_names = ["PostalCode", "Borough", "Neighborhood", "Latitude", "Longitude"]

In [17]:
test_df = pd.DataFrame(columns=column_names)

In [18]:
test_list = ["M5G", "M2H", "M4B", "M1J", "M4G", "M4M", "M1R", "M9V", "M9L", "M5V", "M1B", "M5A"]

In [19]:
for postcode in test_list:
    test_df = test_df.append(df_3[df_3["Postal Code"]==postcode], ignore_index=True)
    
test_df.head()

PostalCode           Borough                     Neighborhood   Latitude  \
0        NaN  Downtown Toronto               Central Bay Street  43.657952   
1        NaN        North York                Hillcrest Village  43.803762   
2        NaN         East York  Parkview Hill, Woodbine Gardens  43.706397   
3        NaN       Scarborough              Scarborough Village  43.744734   
4        NaN         East York                          Leaside  43.709060   

   Longitude Postal Code  
0 -79.387383         M5G  
1 -79.363452         M2H  
2 -79.309937         M4B  
3 -79.239476         M1J  
4 -79.363452         M4G

In [20]:
address = 'Toronto'

In [21]:
geolocator = Nominatim(user_agent="my-application")
location = geolocator.geocode(address)
latitude = location.latitude
longitude = location.longitude
print('The geograpical coordinate of Toronto are {}, {}.'.format(latitude, longitude))

The geograpical coordinate of Toronto are 43.6534817, -79.3839347.


In [22]:
# create map of Toronto using latitude and longitude values
map_toronto = folium.Map(location=[latitude, longitude], zoom_start=10)

# add markers to map
for lat, lng, borough, neighborhood in zip(df_3['Latitude'], df_3['Longitude'], df_3['Borough'], df_3['Neighborhood']):
    label = '{}, {}'.format(neighborhood, borough)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7).add_to(map_toronto)  
    
map_toronto

In [23]:
borough_names = list(df_3.Borough.unique())

borough_with_toronto = []

for x in borough_names:
    if "toronto" in x.lower():
        borough_with_toronto.append(x)
        
borough_with_toronto

['East Toronto', 'Central Toronto', 'Downtown Toronto', 'West Toronto']

In [24]:
toronto_df_new = df_3[df_3['Borough'].isin(borough_with_toronto)].reset_index(drop=True)
print(toronto_df_new.shape)
toronto_df_new.head()

(39, 5)


Postal Code          Borough                    Neighborhood   Latitude  \
0         M4E     East Toronto                     The Beaches  43.676357   
1         M4K     East Toronto    The Danforth West, Riverdale  43.679557   
2         M4L     East Toronto  India Bazaar, The Beaches West  43.668999   
3         M4M     East Toronto                 Studio District  43.659526   
4         M4N  Central Toronto                   Lawrence Park  43.728020   

   Longitude  
0 -79.293031  
1 -79.352188  
2 -79.315572  
3 -79.340923  
4 -79.388790

In [25]:
toronto_df_new

Postal Code           Borough  \
0          M4E      East Toronto   
1          M4K      East Toronto   
2          M4L      East Toronto   
3          M4M      East Toronto   
4          M4N   Central Toronto   
5          M4P   Central Toronto   
6          M4R   Central Toronto   
7          M4S   Central Toronto   
8          M4T   Central Toronto   
9          M4V   Central Toronto   
10         M4W  Downtown Toronto   
11         M4X  Downtown Toronto   
12         M4Y  Downtown Toronto   
13         M5A  Downtown Toronto   
14         M5B  Downtown Toronto   
15         M5C  Downtown Toronto   
16         M5E  Downtown Toronto   
17         M5G  Downtown Toronto   
18         M5H  Downtown Toronto   
19         M5J  Downtown Toronto   
20         M5K  Downtown Toronto   
21         M5L  Downtown Toronto   
22         M5N   Central Toronto   
23         M5P   Central Toronto   
24         M5R   Central Toronto   
25         M5S  Downtown Toronto   
26         M5T  Downtown Toronto   
27         M5V  Downtown Toronto   
28         M5W  Downtown Toronto   
29         M5X  Downtown Toronto   
30         M6G  Downtown Toronto   
31         M6H      West Toronto   
32         M6J      West Toronto   
33         M6K      West Toronto   
34         M6P      West Toronto   
35         M6R      West Toronto   
36         M6S      West Toronto   
37         M7A  Downtown Toronto   
38         M7Y      East Toronto   

                                         Neighborhood   Latitude  Longitude  
0                                         The Beaches  43.676357 -79.293031  
1                        The Danforth West, Riverdale  43.679557 -79.352188  
2                      India Bazaar, The Beaches West  43.668999 -79.315572  
3                                     Studio District  43.659526 -79.340923  
4                                       Lawrence Park  43.728020 -79.388790  
5                                    Davisville North  43.712751 -79.390197  
6                   North Toronto West, Lawrence Park  43.715383 -79.405678  
7                                          Davisville  43.704324 -79.388790  
8                         Moore Park, Summerhill East  43.689574 -79.383160  
9   Summerhill West, Rathnelly, South Hill, Forest...  43.686412 -79.400049  
10                                           Rosedale  43.679563 -79.377529  
11                        St. James Town, Cabbagetown  43.667967 -79.367675  
12                               Church and Wellesley  43.665860 -79.383160  
13                          Regent Park, Harbourfront  43.654260 -79.360636  
14                           Garden District, Ryerson  43.657162 -79.378937  
15                                     St. James Town  43.651494 -79.375418  
16                                        Berczy Park  43.644771 -79.373306  
17                                 Central Bay Street  43.657952 -79.387383  
18                           Richmond, Adelaide, King  43.650571 -79.384568  
19  Harbourfront East, Union Station, Toronto Islands  43.640816 -79.381752  
20           Toronto Dominion Centre, Design Exchange  43.647177 -79.381576  
21                     Commerce Court, Victoria Hotel  43.648198 -79.379817  
22                                           Roselawn  43.711695 -79.416936  
23    Forest Hill North & West, Forest Hill Road Park  43.696948 -79.411307  
24                The Annex, North Midtown, Yorkville  43.672710 -79.405678  
25                     University of Toronto, Harbord  43.662696 -79.400049  
26          Kensington Market, Chinatown, Grange Park  43.653206 -79.400049  
27  CN Tower, King and Spadina, Railway Lands, Har...  43.628947 -79.394420  
28                                     Stn A PO Boxes  43.646435 -79.374846  
29             First Canadian Place, Underground city  43.648429 -79.382280  
30                                           Christie  43.669542 -79.422564  
31                       Dufferin, Dovercourt Village  43.669005 -

In [26]:
map_toronto = folium.Map(location=[latitude, longitude], zoom_start=10)

# add markers to map
for lat, lng, borough, neighborhood in zip(toronto_df_new['Latitude'], toronto_df_new['Longitude'], toronto_df_new['Borough'], toronto_df_new['Neighborhood']):
    label = '{}, {}'.format(neighborhood, borough)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7).add_to(map_toronto)  
    
map_toronto

In [27]:
CLIENT_ID = 'ZX3P2VJMC04BOSEKBCNL0FFQJNVTZNVF44DWB04TPQQJERNG' # your Foursquare ID
CLIENT_SECRET = 'XHO00AB44N2EP1JF4JBY5FMKIUNDGQRABCYEAGYHGQZANOIK' # your Foursquare Secret
VERSION = '20180604'
LIMIT = 30
print('Your credentails:')
print('CLIENT_ID: ' + CLIENT_ID)
print('CLIENT_SECRET:' + CLIENT_SECRET)

Your credentails:
CLIENT_ID: ZX3P2VJMC04BOSEKBCNL0FFQJNVTZNVF44DWB04TPQQJERNG
CLIENT_SECRET:XHO00AB44N2EP1JF4JBY5FMKIUNDGQRABCYEAGYHGQZANOIK


In [29]:
radius = 500
LIMIT = 100

venues = []

for lat, long, post, borough, neighborhood in zip(toronto_df_new['Latitude'], toronto_df_new['Longitude'], toronto_df_new['Postal Code'], toronto_df_new['Borough'], toronto_df_new['Neighborhood']):
    url = "https://api.foursquare.com/v2/venues/explore?client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}".format(
        CLIENT_ID,
        CLIENT_SECRET,
        VERSION,
        lat,
        long,
        radius, 
        LIMIT)
    
    results = requests.get(url).json()["response"]['groups'][0]['items']
    
    for venue in results:
        venues.append((
            post, 
            borough,
            neighborhood,
            lat, 
            long, 
            venue['venue']['name'], 
            venue['venue']['location']['lat'], 
            venue['venue']['location']['lng'],  
            venue['venue']['categories'][0]['name']))

In [30]:
venues_df = pd.DataFrame(venues)

# define the column names
venues_df.columns = ['PostalCode', 'Borough', 'Neighborhood', 'BoroughLatitude', 'BoroughLongitude', 'VenueName', 'VenueLatitude', 'VenueLongitude', 'VenueCategory']

print(venues_df.shape)
venues_df.head()

(1614, 9)


PostalCode       Borough                  Neighborhood  BoroughLatitude  \
0        M4E  East Toronto                   The Beaches        43.676357   
1        M4E  East Toronto                   The Beaches        43.676357   
2        M4E  East Toronto                   The Beaches        43.676357   
3        M4E  East Toronto                   The Beaches        43.676357   
4        M4K  East Toronto  The Danforth West, Riverdale        43.679557   

   BoroughLongitude                           VenueName  VenueLatitude  \
0        -79.293031                   Glen Manor Ravine      43.676821   
1        -79.293031  The Big Carrot Natural Food Market      43.678879   
2        -79.293031                 Grover Pub and Grub      43.679181   
3        -79.293031                       Upper Beaches      43.680563   
4        -79.352188                       MenEssentials      43.677820   

   VenueLongitude      VenueCategory  
0      -79.293942              Trail  
1      -79.297734  Health Food Store  
2      -79.297215                Pub  
3      -79.292869       Neighborhood  
4      -79.351265     Cosmetics Shop

In [31]:
venues_df.groupby(["PostalCode", "Borough", "Neighborhood"]).count()

BoroughLatitude  \
PostalCode Borough          Neighborhood                                                          
M4E        East Toronto     The Beaches                                                       4   
M4K        East Toronto     The Danforth West, Riverdale                                     43   
M4L        East Toronto     India Bazaar, The Beaches West                                   22   
M4M        East Toronto     Studio District                                                  40   
M4N        Central Toronto  Lawrence Park                                                     4   
M4P        Central Toronto  Davisville North                                                  6   
M4R        Central Toronto  North Toronto West, Lawrence Park                                18   
M4S        Central Toronto  Davisville                                                       35   
M4T        Central Toronto  Moore Park, Summerhill East                                       1   
M4V        Central Toronto  Summerhill West, Rathnelly, South Hill, Forest ...               16   
M4W        Downtown Toronto Rosedale                                                          4   
M4X        Downtown Toronto St. James Town, Cabbagetown                                      45   
M4Y        Downtown Toronto Church and Wellesley                                             79   
M5A        Downtown Toronto Regent Park, Harbourfront                                        43   
M5B        Downtown Toronto Garden District, Ryerson                                        100   
M5C        Downtown Toronto St. James Town                                                   80   
M5E        Downtown Toronto Berczy Park                                                      56   
M5G        Downtown Toronto Central Bay Street                                               64   
M5H        Downtown Toronto Richmond, Adelaide, King                                         95   
M5J        Downtown Toronto Harbourfront East, Union Station, Toronto Islands               100   
M5K        Downtown Toronto Toronto Dominion Centre, Design Exchange                        100   
M5L        Downtown Toronto Commerce Court, Victoria Hotel                                  100   
M5N        Central Toronto  Roselawn                                                          2   
M5P        Central Toronto  Forest Hill North & West, Forest Hill Road Park                   4   
M5R        Central Toronto  The Annex, North Midtown, Yorkville                              20   
M5S        Downtown Toronto University of Toronto, Harbord                                   37   
M5T        Downtown Toronto Kensington Market, Chinatown, Grange Park                        60   
M5V        Downtown Toronto CN Tower, King and Spadina, Railway Lands, Harb...               18   
M5W        Downtown Toronto Stn A PO Boxes                                                   94   
M5X        Downtown Toronto First Canadian Place, Underground city                          100   
M6G        Downtown Toronto Christie                                                         16   
M6H        West Toronto     Dufferin, Dovercourt Village                                     16   
M6J        West Toronto     Little Portugal, Trinity                                         45   
M6K        West Toronto     Brockton, Parkdale Village, Exhibition Place                     23   
M6P        West Toronto     High Park, The Junction South                                    23   
M6R        West Toronto     Parkdale, Roncesvalles                                           14   
M6S        West Toronto     Runnymede, Swansea                                               39   
M7A        Downtown Toronto Queen's Park, Ontario Provincial Government                      33   
M7Y        East Toronto     Business reply mail Processing Centre, South Ce...               15   

                    

In [32]:
print('There are {} uniques categories.'.format(len(venues_df['VenueCategory'].unique())))

There are 241 uniques categories.


In [33]:
venues_df['VenueCategory'].unique()[:50]

array(['Trail', 'Health Food Store', 'Pub', 'Neighborhood',
       'Cosmetics Shop', 'Greek Restaurant', 'Italian Restaurant',
       'Ice Cream Shop', 'Yoga Studio', 'Brewery',
       'Fruit & Vegetable Store', 'Dessert Shop', 'Restaurant',
       'Pizza Place', 'Juice Bar', 'Bookstore', 'Bubble Tea Shop',
       'Furniture / Home Store', 'Grocery Store', 'Spa', 'Coffee Shop',
       'Bakery', 'Caribbean Restaurant', 'Café', 'Indian Restaurant',
       'Japanese Restaurant', 'Lounge', 'Frozen Yogurt Shop',
       'American Restaurant', 'Liquor Store', 'Gym', 'Fish & Chips Shop',
       'Fast Food Restaurant', 'Sushi Restaurant', 'Park', 'Pet Store',
       'Steakhouse', 'Burrito Place', 'Movie Theater', 'Sandwich Place',
       'Light Rail Station', 'Food & Drink Shop', 'Fish Market',
       'Gay Bar', 'Seafood Restaurant', 'Cheese Shop',
       'Middle Eastern Restaurant', 'Comfort Food Restaurant',
       'Stationery Store', 'Wine Bar'], dtype=object)

In [34]:
"Japanese Restaurant" in venues_df['VenueCategory'].unique()

True

In [35]:
toronto_onehot = pd.get_dummies(venues_df[['VenueCategory']], prefix="", prefix_sep="")

# add postal, borough and neighborhood column back to dataframe
toronto_onehot['PostalCode'] = venues_df['PostalCode'] 
toronto_onehot['Borough'] = venues_df['Borough'] 
toronto_onehot['Neighborhoods'] = venues_df['Neighborhood'] 

# move postal, borough and neighborhood column to the first column
fixed_columns = list(toronto_onehot.columns[-3:]) + list(toronto_onehot.columns[:-3])
toronto_onehot = toronto_onehot[fixed_columns]

print(toronto_onehot.shape)
toronto_onehot.head()

(1614, 244)


PostalCode       Borough                 Neighborhoods  Afghan Restaurant  \
0        M4E  East Toronto                   The Beaches                  0   
1        M4E  East Toronto                   The Beaches                  0   
2        M4E  East Toronto                   The Beaches                  0   
3        M4E  East Toronto                   The Beaches                  0   
4        M4K  East Toronto  The Danforth West, Riverdale                  0   

   Airport  Airport Food Court  Airport Gate  Airport Lounge  Airport Service  \
0        0                   0             0               0                0   
1        0                   0             0               0                0   
2        0                   0             0               0                0   
3        0                   0             0               0                0   
4        0                   0             0               0                0   

   Airport Terminal  American Restaurant  Antique Shop  Aquarium  Art Gallery  \
0                 0                    0             0         0            0   
1                 0                    0             0         0            0   
2                 0                    0             0         0            0   
3                 0                    0             0         0            0   
4                 0                    0             0         0            0   

   Art Museum  Arts & Crafts Store  Asian Restaurant  BBQ Joint  Baby Store  \
0           0                    0                 0          0           0   
1           0                    0                 0          0           0   
2           0                    0                 0          0           0   
3           0                    0                 0          0           0   
4           0                    0                 0          0           0   

   Bagel Shop  Bakery  Bank  Bar  Baseball Stadium  Basketball Stadium  Beach  \
0           0       0     0    0                 0                   0      0   
1           0       0     0    0                 0                   0      0   
2           0       0     0    0                 0                   0      0   
3           0       0     0    0                 0                   0      0   
4           0       0     0    0                 0                   0      0   

   Bed & Breakfast  Beer Bar  Beer Store  Belgian Restaurant  Bistro  \
0                0         0           0                   0       0   
1                0         0           0                   0       0   
2                0         0           0                   0       0   
3                0         0           0                   0       0   
4                0         0           0                   0       0   

   Boat or Ferry  Bookstore  Boutique  Brazilian Restaurant  Breakfast Spot  \
0              0          0         0                     0               0   
1              0          0         0                     0               0   
2              0          0         0                     0               0   
3              0          0         0                     0               0   
4              0          0         0                     0               0   

   Brewery  Bubble Tea Shop  Building  Burger Joint  Burrito Place  Bus Line  \
0        0                0         0             0              0         0   
1        0                0         0             0              0         0   
2        0                0         0             0              0         0   
3        0                0         0             0              0         0   
4        0                0         0             0              0         0   

   Butcher  Café  Cajun / Creole Restaurant  Camera Store  Candy Store  \
0        0     0                          0             0            0   
1        0     0                          0           

In [36]:
toronto_grouped = toronto_onehot.groupby(["PostalCode", "Borough", "Neighborhoods"]).mean().reset_index()

print(toronto_grouped.shape)
toronto_grouped

(39, 244)


PostalCode           Borough  \
0         M4E      East Toronto   
1         M4K      East Toronto   
2         M4L      East Toronto   
3         M4M      East Toronto   
4         M4N   Central Toronto   
5         M4P   Central Toronto   
6         M4R   Central Toronto   
7         M4S   Central Toronto   
8         M4T   Central Toronto   
9         M4V   Central Toronto   
10        M4W  Downtown Toronto   
11        M4X  Downtown Toronto   
12        M4Y  Downtown Toronto   
13        M5A  Downtown Toronto   
14        M5B  Downtown Toronto   
15        M5C  Downtown Toronto   
16        M5E  Downtown Toronto   
17        M5G  Downtown Toronto   
18        M5H  Downtown Toronto   
19        M5J  Downtown Toronto   
20        M5K  Downtown Toronto   
21        M5L  Downtown Toronto   
22        M5N   Central Toronto   
23        M5P   Central Toronto   
24        M5R   Central Toronto   
25        M5S  Downtown Toronto   
26        M5T  Downtown Toronto   
27        M5V  Downtown Toronto   
28        M5W  Downtown Toronto   
29        M5X  Downtown Toronto   
30        M6G  Downtown Toronto   
31        M6H      West Toronto   
32        M6J      West Toronto   
33        M6K      West Toronto   
34        M6P      West Toronto   
35        M6R      West Toronto   
36        M6S      West Toronto   
37        M7A  Downtown Toronto   
38        M7Y      East Toronto   

                                        Neighborhoods  Afghan Restaurant  \
0                                         The Beaches           0.000000   
1                        The Danforth West, Riverdale           0.000000   
2                      India Bazaar, The Beaches West           0.000000   
3                                     Studio District           0.000000   
4                                       Lawrence Park           0.000000   
5                                    Davisville North           0.000000   
6                   North Toronto West, Lawrence Park           0.000000   
7                                          Davisville           0.000000   
8                         Moore Park, Summerhill East           0.000000   
9   Summerhill West, Rathnelly, South Hill, Forest...           0.000000   
10                                           Rosedale           0.000000   
11                        St. James Town, Cabbagetown           0.000000   
12                               Church and Wellesley           0.012658   
13                          Regent Park, Harbourfront           0.000000   
14                           Garden District, Ryerson           0.000000   
15                                     St. James Town           0.000000   
16                                        Berczy Park           0.000000   
17                                 Central Bay Street           0.000000   
18                           Richmond, Adelaide, King           0.000000   
19  Harbourfront East, Union Station, Toronto Islands           0.000000   
20           Toronto Dominion Centre, Design Exchange           0.000000   
21                     Commerce Court, Victoria Hotel           0.000000   
22                                           Roselawn           0.000000   
23    Forest Hill North & West, Forest Hill Road Park           0.000000   
24                The Annex, North Midtown, Yorkville           0.000000   
25                     University of Toronto, Harbord           0.000000   
26          Kensington Market, Chinatown, Grange Park           0.000000   
27  CN Tower, King and Spadina, Railway Lands, Har...           0.000000   
28                                     Stn A PO Boxes           0.000000   
29             First Canadian Place, Underground city           0.000000   
30                                           Christie           0.000000   
31                       Dufferin, Dovercourt Village           0.000000   
32                           Little Portugal, Trinity           0.000000   
33       Brockton,

In [37]:
len(toronto_grouped[toronto_grouped["Japanese Restaurant"] > 0])

16

In [38]:
toronto_asian = toronto_grouped[["Neighborhoods","Japanese Restaurant"]]

In [39]:
toronto_asian.head()

Neighborhoods  Japanese Restaurant
0                     The Beaches             0.000000
1    The Danforth West, Riverdale             0.023256
2  India Bazaar, The Beaches West             0.000000
3                 Studio District             0.000000
4                   Lawrence Park             0.000000

In [40]:
# set number of clusters
toclusters = 3

to_clustering = toronto_asian.drop(["Neighborhoods"], 1)

# run k-means clustering
kmeans = KMeans(n_clusters=toclusters, random_state=0).fit(to_clustering)

# check cluster labels generated for each row in the dataframe
kmeans.labels_[0:10]

array([0, 1, 0, 0, 0, 0, 0, 0, 0, 0], dtype=int32)

In [41]:
toronto_merged = toronto_asian.copy()

# add clustering labels
toronto_merged["Cluster Labels"] = kmeans.labels_

In [42]:
toronto_merged

Neighborhoods  Japanese Restaurant  \
0                                         The Beaches             0.000000   
1                        The Danforth West, Riverdale             0.023256   
2                      India Bazaar, The Beaches West             0.000000   
3                                     Studio District             0.000000   
4                                       Lawrence Park             0.000000   
5                                    Davisville North             0.000000   
6                   North Toronto West, Lawrence Park             0.000000   
7                                          Davisville             0.000000   
8                         Moore Park, Summerhill East             0.000000   
9   Summerhill West, Rathnelly, South Hill, Forest...             0.000000   
10                                           Rosedale             0.000000   
11                        St. James Town, Cabbagetown             0.022222   
12                               Church and Wellesley             0.050633   
13                          Regent Park, Harbourfront             0.000000   
14                           Garden District, Ryerson             0.030000   
15                                     St. James Town             0.012500   
16                                        Berczy Park             0.017857   
17                                 Central Bay Street             0.031250   
18                           Richmond, Adelaide, King             0.010526   
19  Harbourfront East, Union Station, Toronto Islands             0.010000   
20           Toronto Dominion Centre, Design Exchange             0.030000   
21                     Commerce Court, Victoria Hotel             0.030000   
22                                           Roselawn             0.000000   
23    Forest Hill North & West, Forest Hill Road Park             0.000000   
24                The Annex, North Midtown, Yorkville             0.000000   
25                     University of Toronto, Harbord             0.054054   
26          Kensington Market, Chinatown, Grange Park             0.016667   
27  CN Tower, King and Spadina, Railway Lands, Har...             0.000000   
28                                     Stn A PO Boxes             0.031915   
29             First Canadian Place, Underground city             0.040000   
30                                           Christie             0.000000   
31                       Dufferin, Dovercourt Village             0.000000   
32                           Little Portugal, Trinity             0.022222   
33       Brockton, Parkdale Village, Exhibition Place             0.000000   
34                      High Park, The Junction South             0.000000   
35                             Parkdale, Roncesvalles             0.000000   
36                                 Runnymede, Swansea             0.000000   
37        Queen's Park, Ontario Provincial Government             0.000000   
38  Business reply mail Processing Centre, South C...             0.000000   

    Cluster Labels  
0                0  
1                1  
2                0  
3                0  
4                0  
5                0  
6                0  
7                0  
8                0  
9                0  
10               0  
11               1  
12               2  
13               0  
14               1  
15               0  
16               1  
17               1  
18               0  
19               0  
20               1  
21               1  
22               0  
23               0  
24               0  
25               2  
26               1  
27               0  
28               1  
29               2  
30               0  
31               0  
32               1  
33               0  
34               0  
35               0  
36               0  
37               0  
38               0

In [43]:

# merge toronto_grouped with toronto_data to add latitude/longitude for each neighborhood
toronto_merged = toronto_merged.join(venues_df.set_index("Neighborhood"), on="Neighborhoods")

print(toronto_merged.shape)
toronto_merged.head()

(1614, 11)


Neighborhoods  Japanese Restaurant  Cluster Labels  \
0                   The Beaches             0.000000               0   
0                   The Beaches             0.000000               0   
0                   The Beaches             0.000000               0   
0                   The Beaches             0.000000               0   
1  The Danforth West, Riverdale             0.023256               1   

  PostalCode       Borough  BoroughLatitude  BoroughLongitude  \
0        M4E  East Toronto        43.676357        -79.293031   
0        M4E  East Toronto        43.676357        -79.293031   
0        M4E  East Toronto        43.676357        -79.293031   
0        M4E  East Toronto        43.676357        -79.293031   
1        M4K  East Toronto        43.679557        -79.352188   

                            VenueName  VenueLatitude  VenueLongitude  \
0                   Glen Manor Ravine      43.676821      -79.293942   
0  The Big Carrot Natural Food Market      43.678879      -79.297734   
0                 Grover Pub and Grub      43.679181      -79.297215   
0                       Upper Beaches      43.680563      -79.292869   
1                       MenEssentials      43.677820      -79.351265   

       VenueCategory  
0              Trail  
0  Health Food Store  
0                Pub  
0       Neighborhood  
1     Cosmetics Shop

In [44]:
print(toronto_merged.shape)
toronto_merged.sort_values(["Cluster Labels"], inplace=True)
toronto_merged.head()

(1614, 11)


Neighborhoods  Japanese Restaurant  Cluster Labels PostalCode  \
0                The Beaches             0.000000               0        M4E   
18  Richmond, Adelaide, King             0.010526               0        M5H   
18  Richmond, Adelaide, King             0.010526               0        M5H   
18  Richmond, Adelaide, King             0.010526               0        M5H   
18  Richmond, Adelaide, King             0.010526               0        M5H   

             Borough  BoroughLatitude  BoroughLongitude          VenueName  \
0       East Toronto        43.676357        -79.293031  Glen Manor Ravine   
18  Downtown Toronto        43.650571        -79.384568       McEwan Foods   
18  Downtown Toronto        43.650571        -79.384568         Soup Nutsy   
18  Downtown Toronto        43.650571        -79.384568   Grace O'Malley's   
18  Downtown Toronto        43.650571        -79.384568            Druxy's   

    VenueLatitude  VenueLongitude  VenueCategory  
0       43.676821      -79.293942          Trail  
18      43.647160      -79.381044  Deli / Bodega  
18      43.647858      -79.380533     Soup Place  
18      43.647646      -79.388572            Pub  
18      43.648015      -79.379907  Deli / Bodega

In [45]:
# Matplotlib and associated plotting modules
import matplotlib.cm as cm
import matplotlib.colors as colors

In [48]:
# create map
map_clusters = folium.Map(location=[latitude, longitude], zoom_start=11)

# set color scheme for the clusters
x = np.arange(toclusters)
ys = [i + x + (i*x)**2 for i in range(toclusters)]
colors_array = cm.rainbow(np.linspace(0, 1, len(ys)))
rainbow = [colors.rgb2hex(i) for i in colors_array]

# add markers to the map
markers_colors = []
for lat, lon, poi, cluster in zip(toronto_merged['BoroughLatitude'], toronto_merged['BoroughLongitude'], toronto_merged['Neighborhoods'], toronto_merged['Cluster Labels']):
    label = folium.Popup(str(poi) + ' Cluster ' + str(cluster), parse_html=True)
    folium.CircleMarker(
        [lat, lon],
        radius=5,
        popup=label,
        color=rainbow[cluster-1],
        fill=True,
        fill_color=rainbow[cluster-1],
        fill_opacity=0.7).add_to(map_clusters)
       
map_clusters

In [49]:
#Cluster 0
toronto_merged.loc[toronto_merged['Cluster Labels'] == 0]

Neighborhoods  Japanese Restaurant  \
0                                         The Beaches             0.000000   
18                           Richmond, Adelaide, King             0.010526   
18                           Richmond, Adelaide, King             0.010526   
18                           Richmond, Adelaide, King             0.010526   
18                           Richmond, Adelaide, King             0.010526   
19  Harbourfront East, Union Station, Toronto Islands             0.010000   
19  Harbourfront East, Union Station, Toronto Islands             0.010000   
19  Harbourfront East, Union Station, Toronto Islands             0.010000   
19  Harbourfront East, Union Station, Toronto Islands             0.010000   
19  Harbourfront East, Union Station, Toronto Islands             0.010000   
19  Harbourfront East, Union Station, Toronto Islands             0.010000   
19  Harbourfront East, Union Station, Toronto Islands             0.010000   
19  Harbourfront East, Union Station, Toronto Islands             0.010000   
19  Harbourfront East, Union Station, Toronto Islands             0.010000   
19  Harbourfront East, Union Station, Toronto Islands             0.010000   
19  Harbourfront East, Union Station, Toronto Islands             0.010000   
19  Harbourfront East, Union Station, Toronto Islands             0.010000   
19  Harbourfront East, Union Station, Toronto Islands             0.010000   
19  Harbourfront East, Union Station, Toronto Islands             0.010000   
19  Harbourfront East, Union Station, Toronto Islands             0.010000   
19  Harbourfront East, Union Station, Toronto Islands             0.010000   
19  Harbourfront East, Union Station, Toronto Islands             0.010000   
19  Harbourfront East, Union Station, Toronto Islands             0.010000   
19  Harbourfront East, Union Station, Toronto Islands             0.010000   
19  Harbourfront East, Union Station, Toronto Islands             0.010000   
19  Harbourfront East, Union Station, Toronto Islands             0.010000   
18                           Richmond, Adelaide, King             0.010526   
18                           Richmond, Adelaide, King             0.010526   
18                           Richmond, Adelaide, King             0.010526   
18                           Richmond, Adelaide, King             0.010526   
18                           Richmond, Adelaide, King             0.010526   
18                           Richmond, Adelaide, King             0.010526   
18                           Richmond, Adelaide, King             0.010526   
18                           Richmond, Adelaide, King             0.010526   
18                           Richmond, Adelaide, King             0.010526   
18                           Richmond, Adelaide, King             0.010526   
18                           Richmond, Adelaide, King             0.010526   
18                           Richmond, Adelaide, King             0.010526   
18                           Richmond, Adelaide, King             0.010526   
18                           Richmond, Adelaide, King             0.010526   
18                           Richmond, Adelaide, King             0.010526   
18                           Richmond, Adelaide, King             0.010526   
19  Harbourfront East, Union Station, Toronto Islands             0.010000   
18                           Richmond, Adelaide, King             0.010526   
18                           Richmond, Adelaide, King             0.010526   
18                           Richmond, Adelaide, King             0.010526   
18                           Richmond, Adelaide, King             0.010526   
18                           Richmond, Adelaide, King             0.010526   
18                           Richmond, Adelaide, King             0.010526   
18                           Richmond, Adelaide, King             0.010526   
18                           Richmond, Adelaide, King         

In [69]:
#Cluster 1
toronto_merged.loc[toronto_merged['Cluster Labels'] == 1]

Neighborhoods  Japanese Restaurant  \
20   Toronto Dominion Centre, Design Exchange             0.030000   
20   Toronto Dominion Centre, Design Exchange             0.030000   
11                St. James Town, Cabbagetown             0.022222   
20   Toronto Dominion Centre, Design Exchange             0.030000   
20   Toronto Dominion Centre, Design Exchange             0.030000   
20   Toronto Dominion Centre, Design Exchange             0.030000   
14                   Garden District, Ryerson             0.030000   
20   Toronto Dominion Centre, Design Exchange             0.030000   
20   Toronto Dominion Centre, Design Exchange             0.030000   
20   Toronto Dominion Centre, Design Exchange             0.030000   
20   Toronto Dominion Centre, Design Exchange             0.030000   
20   Toronto Dominion Centre, Design Exchange             0.030000   
14                   Garden District, Ryerson             0.030000   
20   Toronto Dominion Centre, Design Exchange             0.030000   
20   Toronto Dominion Centre, Design Exchange             0.030000   
20   Toronto Dominion Centre, Design Exchange             0.030000   
20   Toronto Dominion Centre, Design Exchange             0.030000   
11                St. James Town, Cabbagetown             0.022222   
20   Toronto Dominion Centre, Design Exchange             0.030000   
14                   Garden District, Ryerson             0.030000   
20   Toronto Dominion Centre, Design Exchange             0.030000   
20   Toronto Dominion Centre, Design Exchange             0.030000   
20   Toronto Dominion Centre, Design Exchange             0.030000   
20   Toronto Dominion Centre, Design Exchange             0.030000   
20   Toronto Dominion Centre, Design Exchange             0.030000   
20   Toronto Dominion Centre, Design Exchange             0.030000   
14                   Garden District, Ryerson             0.030000   
20   Toronto Dominion Centre, Design Exchange             0.030000   
20   Toronto Dominion Centre, Design Exchange             0.030000   
20   Toronto Dominion Centre, Design Exchange             0.030000   
20   Toronto Dominion Centre, Design Exchange             0.030000   
20   Toronto Dominion Centre, Design Exchange             0.030000   
20   Toronto Dominion Centre, Design Exchange             0.030000   
20   Toronto Dominion Centre, Design Exchange             0.030000   
20   Toronto Dominion Centre, Design Exchange             0.030000   
20   Toronto Dominion Centre, Design Exchange             0.030000   
20   Toronto Dominion Centre, Design Exchange             0.030000   
20   Toronto Dominion Centre, Design Exchange             0.030000   
20   Toronto Dominion Centre, Design Exchange             0.030000   
20   Toronto Dominion Centre, Design Exchange             0.030000   
20   Toronto Dominion Centre, Design Exchange             0.030000   
20   Toronto Dominion Centre, Design Exchange             0.030000   
20   Toronto Dominion Centre, Design Exchange             0.030000   
20   Toronto Dominion Centre, Design Exchange             0.030000   
20   Toronto Dominion Centre, Design Exchange             0.030000   
20   Toronto Dominion Centre, Design Exchange             0.030000   
20   Toronto Dominion Centre, Design Exchange             0.030000   
14                   Garden District, Ryerson             0.030000   
14                   Garden District, Ryerson             0.030000   
14                   Garden District, Ryerson             0.030000   
14                   Garden District, Ryerson             0.030000   
14                   Garden District, Ryerson             0.030000   
14                   Garden District, Ryerson             0.030000   
14                   Garden District, Ryerson             0.030000   
14                   Garden District, Ryerson             0.030000   
14                   Garden District, Ryerson             0.030000   
14                   Garden District, Ryer

In [71]:
#Cluster 2
toronto_merged.loc[toronto_merged['Cluster Labels'] == 2]

Neighborhoods  Japanese Restaurant  Cluster Labels  \
12            Church and Wellesley             0.050000               2   
12            Church and Wellesley             0.050000               2   
12            Church and Wellesley             0.050000               2   
12            Church and Wellesley             0.050000               2   
12            Church and Wellesley             0.050000               2   
12            Church and Wellesley             0.050000               2   
12            Church and Wellesley             0.050000               2   
12            Church and Wellesley             0.050000               2   
12            Church and Wellesley             0.050000               2   
12            Church and Wellesley             0.050000               2   
12            Church and Wellesley             0.050000               2   
12            Church and Wellesley             0.050000               2   
12            Church and Wellesley             0.050000               2   
12            Church and Wellesley             0.050000               2   
12            Church and Wellesley             0.050000               2   
12            Church and Wellesley             0.050000               2   
12            Church and Wellesley             0.050000               2   
12            Church and Wellesley             0.050000               2   
12            Church and Wellesley             0.050000               2   
12            Church and Wellesley             0.050000               2   
12            Church and Wellesley             0.050000               2   
12            Church and Wellesley             0.050000               2   
12            Church and Wellesley             0.050000               2   
12            Church and Wellesley             0.050000               2   
12            Church and Wellesley             0.050000               2   
12            Church and Wellesley             0.050000               2   
12            Church and Wellesley             0.050000               2   
12            Church and Wellesley             0.050000               2   
12            Church and Wellesley             0.050000               2   
12            Church and Wellesley             0.050000               2   
12            Church and Wellesley             0.050000               2   
12            Church and Wellesley             0.050000               2   
12            Church and Wellesley             0.050000               2   
12            Church and Wellesley             0.050000               2   
12            Church and Wellesley             0.050000               2   
12            Church and Wellesley             0.050000               2   
12            Church and Wellesley             0.050000               2   
12            Church and Wellesley             0.050000               2   
12            Church and Wellesley             0.050000               2   
12            Church and Wellesley             0.050000               2   
12            Church and Wellesley             0.050000               2   
12            Church and Wellesley             0.050000               2   
12            Church and Wellesley             0.050000               2   
12            Church and Wellesley             0.050000               2   
12            Church and Wellesley             0.050000               2   
12            Church and Wellesley             0.050000               2   
12            Church and Wellesley             0.050000               2   
12            Church and Wellesley             0.050000               2   
12            Church and Wellesley             0.050000               2   
12            Church and Wellesley             0.050000               2   
12            Church and Wellesley             0.050000               2   
12            Church and Wellesley             0.050000               2   
12            Church and Wellesley            